In [2]:
import pandas as pd
import numpy as np
from sklearn import tree
from sklearn import preprocessing
import matplotlib.pyplot as plt

In [3]:
titanic_train = pd.read_csv("train.csv")
titanic_train.head(4)

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S

# Will classify the Data set using Decision tree

# 1. Handel missing values

In [4]:
titanic_train.isna().sum()

PassengerId      0
Survived         0
Pclass           0
Name             0
Sex              0
Age              0
SibSp            0
Parch            0
Ticket           0
Fare             0
Cabin          687
Embarked         0
dtype: int64

In [5]:
titanic_train.drop(['Cabin', 'PassengerId'], axis=1, inplace=True) #droped cabin cuzz it had a lot of null values

## 2. Converting object dtype to int dtype

In [6]:
label_encoder = preprocessing.LabelEncoder()

In [7]:
titanic_train['Sex']=label_encoder.fit_transform(titanic_train['Sex'])
titanic_train['Embarked']=label_encoder.fit_transform(titanic_train['Embarked'])

## 3. Assigning DV & IDV

In [8]:
x = titanic_train[['Sex', 'Age', 'SibSp',  'Parch', 'Fare', 'Embarked']]  #independent variable
y = titanic_train['Survived']                                             # dependent variable 

## 4. Creating model

In [9]:
tree_model = tree.DecisionTreeClassifier(max_depth=12)

In [10]:
tree_model.fit(x,y)

DecisionTreeClassifier(max_depth=12)

## 5. Visvulising the classified data

In [11]:
with open ('Dtree_titiani_train.dot', 'w') as f:
    f= tree.export_graphviz(tree_model, feature_names= ['Sex', 'Age', 'SibSp', 'Parch', 'Fare', 'Embarked'], out_file=f);

In [12]:
plt.rcParams["figure.figsize"] = (300,100)

In [13]:
tree.plot_tree(tree_model,filled = True);

## 6. Model Accuray

In [14]:
print(f"Model Accuracy = {tree_model.score(x,y)*100} %")

Model Accuracy = 93.47581552305961 %


# Now we will select main features with Random forest and then will predict the output of the test data set

In [15]:
from sklearn.ensemble import RandomForestClassifier

In [16]:
rf_model = RandomForestClassifier(n_estimators=1000, max_features=2, oob_score=True)

In [17]:
feature = titanic_train[['Pclass', 'Sex', 'Age', 'SibSp', 'Parch', 'Fare', 'Embarked']]

In [18]:
rf_model.fit(x, y= titanic_train['Survived'])

RandomForestClassifier(max_features=2, n_estimators=1000, oob_score=True)

In [19]:
print(rf_model.oob_score_);

0.8020247469066367


In [20]:
for feature,importance in zip(feature,tree_model.feature_importances_):
    print(feature,'-',importance)

Pclass - 0.3707081300680386
Sex - 0.21306761454340406
Age - 0.08738844629599615
SibSp - 0.030540171537095324
Parch - 0.2727015097468289
Fare - 0.02559412780863698


# Important feature -:
1. Sex
2. Pclass
3. Age

# Creating models with important features

In [21]:
imp_fea = titanic_train[['Sex', 'Pclass', 'Age']]

In [22]:
tree_model_feature = tree.DecisionTreeClassifier(max_depth=6)
tree_model_feature.fit(imp_fea,y)

DecisionTreeClassifier(max_depth=6)

In [23]:
print(f"Model Accuracy = {tree_model_feature.score(imp_fea,y)*100} %")

Model Accuracy = 83.12710911136108 %


# Analysis
1. As we can see the Score of model with Random Forest method is LESS the Score of model without it. so predicting output with the first model only. 

In [24]:
titanic_test = pd.read_csv("test.csv")

In [25]:
titanic_test.isna().sum()

PassengerId    0
Pclass         0
Name           0
Sex            0
Age            0
SibSp          0
Parch          0
Ticket         0
Fare           0
Embarked       0
dtype: int64

In [26]:
titanic_test['Sex']=label_encoder.fit_transform(titanic_test['Sex'])
titanic_test['Embarked']=label_encoder.fit_transform(titanic_test['Embarked'])

In [27]:
feature_list = titanic_test[['Sex', 'Age', 'SibSp',  'Parch', 'Fare', 'Embarked']]

In [28]:
test_pred = tree_model.predict(feature_list)

In [29]:
predicted_output = pd.DataFrame({"PassengerId":titanic_test['PassengerId'], "Survived":test_pred})

In [32]:
predicted_output.to_csv("Output File Of Titanic.csv", index=False)

In [31]:
#Done